In [1]:
import numpy as np
import pandas as pd
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
from sklearn.preprocessing import StandardScaler,MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_squared_error
from dbn.tensorflow import SupervisedDBNRegression,UnsupervisedDBN
from sklearn.model_selection import TimeSeriesSplit
from tensorflow.keras import Sequential, layers, callbacks
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score, mean_squared_error
import matplotlib.pyplot as plt

Instructions for updating:
non-resource variables are not supported in the long term


In [2]:
df = pd.read_csv('yol_65x.csv').set_index('year_month')
scalerx = StandardScaler()
scalery = StandardScaler()
borehole = 'D4N0065'
figname = "p65x.jpeg"
bbh = "BH0065"

In [3]:
MMS = MinMaxScaler()

In [4]:
def extract(lst):
    return [[el] for el in lst]
ydf = df[borehole]
ydf = extract(ydf)
df = pd.DataFrame(scalerx.fit_transform(df), columns=df.columns, index=df.index)
df = df.reset_index()
df['dex'] = df['year_month']
df = df.set_index('year_month')
ydf = scalery.fit_transform(ydf)
# df = df.drop(["Abstraction_log"], axis = 1)
X = np.array(df.drop([borehole], axis = 1).reset_index(drop=True))
Y = np.array(df[borehole])
df

Discharge_log  Temperature_log  precip_trend_log  Abstraction_log  \
year_month                                                                      
1975-06-01       1.241841        -8.125773         -9.601070        -3.235919   
1975-07-01       1.088907        -8.125773         -9.601070        -3.235919   
1975-08-01       0.949992        -8.125773          1.329527        -3.235919   
1975-09-01       0.937809        -0.734924          1.456258        -3.235919   
1975-10-01       0.417940        -0.774786          1.537873        -3.235919   
...                   ...              ...               ...              ...   
1997-10-01       0.160808        -1.004411         -0.071617         1.261857   
1997-11-01       0.131616        -0.461644         -0.128658         1.261857   
1997-12-01       0.119885        -0.106493         -0.332167         1.261857   
1998-01-01       0.039875         0.093327         -0.454876         1.262722   
1998-02-01      -0.002190         0.256065         -0.490173         1.262722   

                 t_1       t_2   D4N0065         dex  
year_month                                            
1975-06-01  8.017062  7.189756  1.364841  1975-06-01  
1975-07-01  1.162163  7.189756  1.400569  1975-07-01  
1975-08-01  1.193403  1.018415  1.437489  1975-08-01  
1975-09-01  1.225684  1.046539  1.474408  1975-09-01  
1975-10-01  1.257966  1.075602  1.510137  1975-10-01  
...              ...       ...       ...         ...  
1997-10-01 -0.631226 -0.369303 -0.448911  1997-10-01  
1997-11-01 -0.423727 -0.596142 -0.451767  1997-11-01  
1997-12-01 -0.426224 -0.409334 -0.454530  1997-12-01  
1998-01-01 -0.428640 -0.411582 -0.457386  1998-01-01  
1998-02-01 -0.431137 -0.413757 -0.540732  1998-02-01  

[273 rows x 8 columns]

In [5]:
def ave(lis):
    return sum(lis)/ len(lis)

In [6]:
trials = 10
dbn_ave_r2 = []
gru_ave_r2 = []
lstm_ave_r2 = []
lstm_gru_ave_r2 = []
ffnn_ave_r2 = []
dbn_lstm_ave_r2 = []
dbn_lstm_blind_r2 = []

dbn_ave_mse = []
gru_ave_mse = []
lstm_ave_mse = []
lstm_gru_ave_mse = []
dbn_lstm_ave_mse = []
ffnn_ave_mse = []
dbn_lstm_blind_mse = []

## DBN

In [7]:
from sklearn.model_selection import TimeSeriesSplit


tss = TimeSeriesSplit(n_splits = 5)
for train_index, test_index in tss.split(X):
    X_train, X_test = X[train_index, :], X[test_index,:]
    Y_train, Y_test = Y[train_index], Y[test_index]

dummyXtest = pd.DataFrame(X_test)
dummyXtest.columns = ['a','b','c','d','e','f', 'g']
# dummyXtest.columns = ['a','b','d','e','f', 'g']
X_test = np.array(dummyXtest.drop(['g'], axis = 1).reset_index(drop=True))

dummyXtrain = pd.DataFrame(X_train)
dummyXtrain.columns = ['a','b','c','d','e','f', 'g']
# dummyXtrain.columns = ['a','b','d','e','f', 'g']

X_train = np.array(dummyXtrain.drop(['g'], axis = 1).reset_index(drop=True))


print (X_train.shape, Y_train.shape)
print (X_test.shape, Y_test.shape)


(228, 6) (228,)
(45, 6) (45,)


In [8]:
regress = SupervisedDBNRegression(hidden_layers_structure = [32, 16],
learning_rate_rbm=0.05,
learning_rate=0.03,
n_epochs_rbm=10,
n_iter_backprop=1000,
batch_size=50,
activation_function='relu',
dropout_p=0.1)

for i in range(trials):
    print("TRIAL: ", i+1)
    print("\n")
    regress.fit(X_train, Y_train)
    dnb_y_pred = regress.predict(X_test)
    dbn_r2 = r2_score(Y_test.tolist(), dnb_y_pred)
    dbn_mse = mean_squared_error(Y_test.tolist(), dnb_y_pred)
    dbn_ave_r2.append(dbn_r2)
    dbn_ave_mse.append(dbn_mse)
    print("\n")

TRIAL:  1


[START] Pre-training step:
Instructions for updating:
Use `tf.cast` instead.
>> Epoch 1 finished 	RBM Reconstruction error 6.155252
>> Epoch 2 finished 	RBM Reconstruction error 5.668619
>> Epoch 3 finished 	RBM Reconstruction error 4.679134
>> Epoch 4 finished 	RBM Reconstruction error 4.151182
>> Epoch 5 finished 	RBM Reconstruction error 4.431393
>> Epoch 6 finished 	RBM Reconstruction error 4.744212
>> Epoch 7 finished 	RBM Reconstruction error 5.639434
>> Epoch 8 finished 	RBM Reconstruction error 6.415633
>> Epoch 9 finished 	RBM Reconstruction error 7.413936
>> Epoch 10 finished 	RBM Reconstruction error 8.746263
>> Epoch 1 finished 	RBM Reconstruction error 10.025534
>> Epoch 2 finished 	RBM Reconstruction error 11.264709
>> Epoch 3 finished 	RBM Reconstruction error 16.379005
>> Epoch 4 finished 	RBM Reconstruction error 23.750269
>> Epoch 5 finished 	RBM Reconstruction error 34.557224
>> Epoch 6 finished 	RBM Reconstruction error 35.495636
>> Epoch 7 finished 	RBM

>> Epoch 159 finished 	ANN training loss 0.111571
>> Epoch 160 finished 	ANN training loss 0.121849
>> Epoch 161 finished 	ANN training loss 0.111854
>> Epoch 162 finished 	ANN training loss 0.119564
>> Epoch 163 finished 	ANN training loss 0.110424
>> Epoch 164 finished 	ANN training loss 0.131561
>> Epoch 165 finished 	ANN training loss 0.117807
>> Epoch 166 finished 	ANN training loss 0.110240
>> Epoch 167 finished 	ANN training loss 0.119947
>> Epoch 168 finished 	ANN training loss 0.111451
>> Epoch 169 finished 	ANN training loss 0.107988
>> Epoch 170 finished 	ANN training loss 0.118829
>> Epoch 171 finished 	ANN training loss 0.114166
>> Epoch 172 finished 	ANN training loss 0.107728
>> Epoch 173 finished 	ANN training loss 0.122092
>> Epoch 174 finished 	ANN training loss 0.107291
>> Epoch 175 finished 	ANN training loss 0.120432
>> Epoch 176 finished 	ANN training loss 0.136279
>> Epoch 177 finished 	ANN training loss 0.107507
>> Epoch 178 finished 	ANN training loss 0.108244


>> Epoch 343 finished 	ANN training loss 0.092743
>> Epoch 344 finished 	ANN training loss 0.097465
>> Epoch 345 finished 	ANN training loss 0.095098
>> Epoch 346 finished 	ANN training loss 0.092080
>> Epoch 347 finished 	ANN training loss 0.095075
>> Epoch 348 finished 	ANN training loss 0.102796
>> Epoch 349 finished 	ANN training loss 0.092333
>> Epoch 350 finished 	ANN training loss 0.097916
>> Epoch 351 finished 	ANN training loss 0.093868
>> Epoch 352 finished 	ANN training loss 0.096177
>> Epoch 353 finished 	ANN training loss 0.108036
>> Epoch 354 finished 	ANN training loss 0.091255
>> Epoch 355 finished 	ANN training loss 0.094945
>> Epoch 356 finished 	ANN training loss 0.096584
>> Epoch 357 finished 	ANN training loss 0.096789
>> Epoch 358 finished 	ANN training loss 0.097973
>> Epoch 359 finished 	ANN training loss 0.102412
>> Epoch 360 finished 	ANN training loss 0.109192
>> Epoch 361 finished 	ANN training loss 0.104826
>> Epoch 362 finished 	ANN training loss 0.091997


>> Epoch 513 finished 	ANN training loss 0.100812
>> Epoch 514 finished 	ANN training loss 0.107053
>> Epoch 515 finished 	ANN training loss 0.114327
>> Epoch 516 finished 	ANN training loss 0.093197
>> Epoch 517 finished 	ANN training loss 0.087497
>> Epoch 518 finished 	ANN training loss 0.091467
>> Epoch 519 finished 	ANN training loss 0.093045
>> Epoch 520 finished 	ANN training loss 0.089168
>> Epoch 521 finished 	ANN training loss 0.107558
>> Epoch 522 finished 	ANN training loss 0.089722
>> Epoch 523 finished 	ANN training loss 0.093876
>> Epoch 524 finished 	ANN training loss 0.089305
>> Epoch 525 finished 	ANN training loss 0.091934
>> Epoch 526 finished 	ANN training loss 0.088568
>> Epoch 527 finished 	ANN training loss 0.099725
>> Epoch 528 finished 	ANN training loss 0.104918
>> Epoch 529 finished 	ANN training loss 0.089119
>> Epoch 530 finished 	ANN training loss 0.093282
>> Epoch 531 finished 	ANN training loss 0.091645
>> Epoch 532 finished 	ANN training loss 0.099239


>> Epoch 694 finished 	ANN training loss 0.085977
>> Epoch 695 finished 	ANN training loss 0.093156
>> Epoch 696 finished 	ANN training loss 0.086975
>> Epoch 697 finished 	ANN training loss 0.085539
>> Epoch 698 finished 	ANN training loss 0.089326
>> Epoch 699 finished 	ANN training loss 0.086223
>> Epoch 700 finished 	ANN training loss 0.093630
>> Epoch 701 finished 	ANN training loss 0.087421
>> Epoch 702 finished 	ANN training loss 0.086878
>> Epoch 703 finished 	ANN training loss 0.094259
>> Epoch 704 finished 	ANN training loss 0.085081
>> Epoch 705 finished 	ANN training loss 0.090694
>> Epoch 706 finished 	ANN training loss 0.102451
>> Epoch 707 finished 	ANN training loss 0.096994
>> Epoch 708 finished 	ANN training loss 0.091764
>> Epoch 709 finished 	ANN training loss 0.089001
>> Epoch 710 finished 	ANN training loss 0.089841
>> Epoch 711 finished 	ANN training loss 0.090636
>> Epoch 712 finished 	ANN training loss 0.085266
>> Epoch 713 finished 	ANN training loss 0.088659


...

>> Epoch 98 finished 	ANN training loss 0.179158
>> Epoch 99 finished 	ANN training loss 0.174432
>> Epoch 100 finished 	ANN training loss 0.173833
>> Epoch 101 finished 	ANN training loss 0.178561
>> Epoch 102 finished 	ANN training loss 0.178180
>> Epoch 103 finished 	ANN training loss 0.172218
>> Epoch 104 finished 	ANN training loss 0.169306
>> Epoch 105 finished 	ANN training loss 0.169133
>> Epoch 106 finished 	ANN training loss 0.186060
>> Epoch 107 finished 	ANN training loss 0.172852
>> Epoch 108 finished 	ANN training loss 0.170056
>> Epoch 109 finished 	ANN training loss 0.170081
>> Epoch 110 finished 	ANN training loss 0.168234
>> Epoch 111 finished 	ANN training loss 0.182022
>> Epoch 112 finished 	ANN training loss 0.168617
>> Epoch 113 finished 	ANN training loss 0.161210
>> Epoch 114 finished 	ANN training loss 0.163596
>> Epoch 115 finished 	ANN training loss 0.160303
>> Epoch 116 finished 	ANN training loss 0.157213
>> Epoch 117 finished 	ANN training loss 0.158049
>>

>> Epoch 299 finished 	ANN training loss 0.111685
>> Epoch 300 finished 	ANN training loss 0.112111
>> Epoch 301 finished 	ANN training loss 0.115878
>> Epoch 302 finished 	ANN training loss 0.110732
>> Epoch 303 finished 	ANN training loss 0.112063
>> Epoch 304 finished 	ANN training loss 0.111638
>> Epoch 305 finished 	ANN training loss 0.107877
>> Epoch 306 finished 	ANN training loss 0.112018
>> Epoch 307 finished 	ANN training loss 0.112169
>> Epoch 308 finished 	ANN training loss 0.109778
>> Epoch 309 finished 	ANN training loss 0.112578
>> Epoch 310 finished 	ANN training loss 0.107540
>> Epoch 311 finished 	ANN training loss 0.109415
>> Epoch 312 finished 	ANN training loss 0.108922
>> Epoch 313 finished 	ANN training loss 0.109223
>> Epoch 314 finished 	ANN training loss 0.116151
>> Epoch 315 finished 	ANN training loss 0.110920
>> Epoch 316 finished 	ANN training loss 0.108834
>> Epoch 317 finished 	ANN training loss 0.109851
>> Epoch 318 finished 	ANN training loss 0.108823


>> Epoch 498 finished 	ANN training loss 0.099794
>> Epoch 499 finished 	ANN training loss 0.096509
>> Epoch 500 finished 	ANN training loss 0.095155
>> Epoch 501 finished 	ANN training loss 0.100114
>> Epoch 502 finished 	ANN training loss 0.099940
>> Epoch 503 finished 	ANN training loss 0.093303
>> Epoch 504 finished 	ANN training loss 0.100042
>> Epoch 505 finished 	ANN training loss 0.096036
>> Epoch 506 finished 	ANN training loss 0.097478
>> Epoch 507 finished 	ANN training loss 0.095122
>> Epoch 508 finished 	ANN training loss 0.100887
>> Epoch 509 finished 	ANN training loss 0.100830
>> Epoch 510 finished 	ANN training loss 0.095548
>> Epoch 511 finished 	ANN training loss 0.095624
>> Epoch 512 finished 	ANN training loss 0.097043
>> Epoch 513 finished 	ANN training loss 0.094274
>> Epoch 514 finished 	ANN training loss 0.093487
>> Epoch 515 finished 	ANN training loss 0.091371
>> Epoch 516 finished 	ANN training loss 0.096189
>> Epoch 517 finished 	ANN training loss 0.093924


>> Epoch 698 finished 	ANN training loss 0.086982
>> Epoch 699 finished 	ANN training loss 0.091017
>> Epoch 700 finished 	ANN training loss 0.087245
>> Epoch 701 finished 	ANN training loss 0.087012
>> Epoch 702 finished 	ANN training loss 0.087811
>> Epoch 703 finished 	ANN training loss 0.089777
>> Epoch 704 finished 	ANN training loss 0.092638
>> Epoch 705 finished 	ANN training loss 0.097575
>> Epoch 706 finished 	ANN training loss 0.089028
>> Epoch 707 finished 	ANN training loss 0.091473
>> Epoch 708 finished 	ANN training loss 0.088602
>> Epoch 709 finished 	ANN training loss 0.091226
>> Epoch 710 finished 	ANN training loss 0.090857
>> Epoch 711 finished 	ANN training loss 0.088009
>> Epoch 712 finished 	ANN training loss 0.093018
>> Epoch 713 finished 	ANN training loss 0.092724
>> Epoch 714 finished 	ANN training loss 0.093900
>> Epoch 715 finished 	ANN training loss 0.088755
>> Epoch 716 finished 	ANN training loss 0.088124
>> Epoch 717 finished 	ANN training loss 0.087111


>> Epoch 889 finished 	ANN training loss 0.089540
>> Epoch 890 finished 	ANN training loss 0.083453
>> Epoch 891 finished 	ANN training loss 0.083394
>> Epoch 892 finished 	ANN training loss 0.087518
>> Epoch 893 finished 	ANN training loss 0.082147
>> Epoch 894 finished 	ANN training loss 0.087948
>> Epoch 895 finished 	ANN training loss 0.084211
>> Epoch 896 finished 	ANN training loss 0.086984
>> Epoch 897 finished 	ANN training loss 0.092537
>> Epoch 898 finished 	ANN training loss 0.092841
>> Epoch 899 finished 	ANN training loss 0.084819
>> Epoch 900 finished 	ANN training loss 0.086613
>> Epoch 901 finished 	ANN training loss 0.090701
>> Epoch 902 finished 	ANN training loss 0.086173
>> Epoch 903 finished 	ANN training loss 0.085106
>> Epoch 904 finished 	ANN training loss 0.090888
>> Epoch 905 finished 	ANN training loss 0.088489
>> Epoch 906 finished 	ANN training loss 0.085028
>> Epoch 907 finished 	ANN training loss 0.088163
>> Epoch 908 finished 	ANN training loss 0.087400


In [9]:
dbn_r2_new = ave(dbn_ave_r2)
dbn_mse_new = ave(dbn_ave_mse)
dbn_ave_r2

[0.5374937320555246,
 0.5355747960538493,
 0.5360010892164131,
 0.5321183956419067,
 0.5505306099165949,
 0.268246949354371,
 0.4943332622525761,
 0.537576098394793,
 0.5193865000752109,
 0.39119274147523]

## RECURRENT NEURAL NETWORKS

In [10]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, LSTM, Dropout, GRU, Bidirectional
from sklearn.preprocessing import MinMaxScaler
from tensorflow.keras import Sequential, layers, callbacks

In [11]:
Y = Y.reshape(-1,1)

from sklearn.model_selection import TimeSeriesSplit
tss = TimeSeriesSplit(n_splits = 5)
for train_index, test_index in tss.split(X):
    X_train, X_test = X[train_index, :], X[test_index,:]
    y_train, y_test = Y[train_index], Y[test_index]

dXtrain = pd.DataFrame(X_train)
dXtrain.columns = ['a','b','c','d','e','f', 'g']
X_train = np.array(dXtrain.drop(['g'], axis = 1).reset_index(drop=True))

dXtest = pd.DataFrame(X_test)
dXtest.columns = ['a','b','c','d','e','f', 'g']
X_test = np.array(dXtest.drop(['g'], axis = 1).reset_index(drop=True))


print (X_train.shape, y_train.shape)
print (X_test.shape, y_test.shape)

(228, 6) (228, 1)
(45, 6) (45, 1)


In [12]:
def forecast(model, test_forecast, gwl, steps_ahead):
    y_pred = []
    current_output = gwl
    for step in range(steps_ahead):
        #print(test_forecast[step])
        input_test = np.concatenate([test_forecast[step][:-1], [current_output]])
        #input_test = [test_forecast[0][0][:-1], gwl]
        #print(input_test)
        pred = model.predict(input_test.reshape(1,1,6))
        y_pred.append(pred[0][0])
        #print(pred)
        current_output = pred[0][0]

    return y_pred

In [13]:
gwl = y_test[0][0]
steps_ahead = X_test.shape[0]
gwl

-0.817593807780658

## LSTM

In [14]:
from tensorflow.keras.optimizers import Adam
from sklearn.metrics import *
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping

import numpy as np
import csv  

# rounding off
Round = 3      

test_pred_lstm  = [] 

for fold in range(trials):
    print(f'Running trial {fold+1}')
    print(X_train.shape)
    
    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))


    check = ModelCheckpoint('model.h5', verbose=1, save_best_only=True)

    early = EarlyStopping(patience=100)

    optimizer = Adam(lr=0.00001)
    model = Sequential()
    model.add(LSTM(50, input_shape=(1, 6)))
    model.add(Dropout(0.1))

    model.add(Dense(1))

    model.compile(loss='mse', optimizer='rmsprop', metrics=['mse'])

    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))


    history = model.fit(X_t_reshaped, 
                    y_train, 
                    validation_split = 0.2,
                    epochs=1000, 
                    batch_size=96, 
                    verbose=1, callbacks=[check, early])
    X_val_reshaped = X_val_reshaped.reshape(X_test.shape[0], 6)

    #running function
    test_forecast = X_test
    y_lstm = forecast(model, test_forecast, gwl, steps_ahead)
    y_lstm = np.array(y_lstm)
    
    #metrics for test
    test_pred_lstm.append(y_lstm)
    mse_lstm = mean_squared_error(y_test, y_lstm)
    r2_lstm = r2_score(y_test, y_lstm)
    lstm_ave_r2.append(r2_lstm)
    lstm_ave_mse.append(mse_lstm)
    

Running trial 1
(228, 6)
Instructions for updating:
If using Keras pass *_constraint arguments to layers.
Train on 182 samples, validate on 46 samples
Epoch 1/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9280 - mean_squared_error: 0.9280
Epoch 00001: val_loss improved from inf to 0.58746, saving model to model.h5
182/182 [==============================] - 1s 4ms/sample - loss: 1.0210 - mean_squared_error: 1.0210 - val_loss: 0.5875 - val_mean_squared_error: 0.5875
Epoch 2/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.8823 - mean_squared_error: 0.8823
Epoch 00002: val_loss improved from 0.58746 to 0.56399, saving model to model.h5
182/182 [==============================] - 0s 150us/sample - loss: 0.8968 - mean_squared_error: 0.8968 - val_loss: 0.5640 - val_mean_squared_error: 0.5640
Epoch 3/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.0600 - mean_squared_error: 1.0600
Epoch 00003: val_loss improved from 0.56399 to 0.54437, sav

Epoch 00023: val_loss improved from 0.27228 to 0.25835, saving model to model.h5
182/182 [==============================] - 0s 139us/sample - loss: 0.2280 - mean_squared_error: 0.2280 - val_loss: 0.2583 - val_mean_squared_error: 0.2583
Epoch 24/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.2164 - mean_squared_error: 0.2164
Epoch 00024: val_loss improved from 0.25835 to 0.24486, saving model to model.h5
182/182 [==============================] - 0s 153us/sample - loss: 0.2219 - mean_squared_error: 0.2219 - val_loss: 0.2449 - val_mean_squared_error: 0.2449
Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.2098 - mean_squared_error: 0.2098
Epoch 00025: val_loss improved from 0.24486 to 0.23126, saving model to model.h5
182/182 [==============================] - 0s 143us/sample - loss: 0.2152 - mean_squared_error: 0.2152 - val_loss: 0.2313 - val_mean_squared_error: 0.2313
Epoch 26/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0

 96/182 [==============>...............] - ETA: 0s - loss: 0.1226 - mean_squared_error: 0.1226
Epoch 00047: val_loss improved from 0.10132 to 0.09980, saving model to model.h5
182/182 [==============================] - 0s 139us/sample - loss: 0.1262 - mean_squared_error: 0.1262 - val_loss: 0.0998 - val_mean_squared_error: 0.0998
Epoch 48/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0876 - mean_squared_error: 0.0876
Epoch 00048: val_loss improved from 0.09980 to 0.09904, saving model to model.h5
182/182 [==============================] - 0s 139us/sample - loss: 0.1271 - mean_squared_error: 0.1271 - val_loss: 0.0990 - val_mean_squared_error: 0.0990
Epoch 49/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0932 - mean_squared_error: 0.0932
Epoch 00049: val_loss improved from 0.09904 to 0.09736, saving model to model.h5
182/182 [==============================] - 0s 142us/sample - loss: 0.1237 - mean_squared_error: 0.1237 - val_loss: 0.0974 - val_mean_s

Epoch 72/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0754 - mean_squared_error: 0.0754
Epoch 00072: val_loss did not improve from 0.08774
182/182 [==============================] - 0s 44us/sample - loss: 0.1006 - mean_squared_error: 0.1006 - val_loss: 0.0878 - val_mean_squared_error: 0.0878
Epoch 73/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0876 - mean_squared_error: 0.0876
Epoch 00073: val_loss improved from 0.08774 to 0.08763, saving model to model.h5
182/182 [==============================] - 0s 143us/sample - loss: 0.1116 - mean_squared_error: 0.1116 - val_loss: 0.0876 - val_mean_squared_error: 0.0876
Epoch 74/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0877 - mean_squared_error: 0.0877
Epoch 00074: val_loss improved from 0.08763 to 0.08676, saving model to model.h5
182/182 [==============================] - 0s 144us/sample - loss: 0.1040 - mean_squared_error: 0.1040 - val_loss: 0.0868 - val_mean_squared_error: 0.0

 96/182 [==============>...............] - ETA: 0s - loss: 0.0797 - mean_squared_error: 0.0797
Epoch 00097: val_loss improved from 0.08524 to 0.08447, saving model to model.h5
182/182 [==============================] - 0s 148us/sample - loss: 0.0970 - mean_squared_error: 0.0970 - val_loss: 0.0845 - val_mean_squared_error: 0.0845
Epoch 98/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1087 - mean_squared_error: 0.1087
Epoch 00098: val_loss did not improve from 0.08447
182/182 [==============================] - 0s 38us/sample - loss: 0.0857 - mean_squared_error: 0.0857 - val_loss: 0.0848 - val_mean_squared_error: 0.0848
Epoch 99/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1087 - mean_squared_error: 0.1087
Epoch 00099: val_loss did not improve from 0.08447
182/182 [==============================] - 0s 46us/sample - loss: 0.0933 - mean_squared_error: 0.0933 - val_loss: 0.0850 - val_mean_squared_error: 0.0850
Epoch 100/1000
 96/182 [==============>..

...

 96/182 [==============>...............] - ETA: 0s - loss: 0.1058 - mean_squared_error: 0.1058
Epoch 00110: val_loss did not improve from 0.08386
182/182 [==============================] - 0s 44us/sample - loss: 0.0858 - mean_squared_error: 0.0858 - val_loss: 0.0845 - val_mean_squared_error: 0.0845
Epoch 111/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0734 - mean_squared_error: 0.0734
Epoch 00111: val_loss did not improve from 0.08386
182/182 [==============================] - 0s 44us/sample - loss: 0.0965 - mean_squared_error: 0.0965 - val_loss: 0.0841 - val_mean_squared_error: 0.0841
Epoch 112/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1128 - mean_squared_error: 0.1128
Epoch 00112: val_loss did not improve from 0.08386
182/182 [==============================] - 0s 44us/sample - loss: 0.0959 - mean_squared_error: 0.0959 - val_loss: 0.0845 - val_mean_squared_error: 0.0845
Epoch 113/1000
 96/182 [==============>...............] - ETA: 0s - lo

Epoch 136/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0921 - mean_squared_error: 0.0921
Epoch 00136: val_loss did not improve from 0.08180
182/182 [==============================] - 0s 55us/sample - loss: 0.0756 - mean_squared_error: 0.0756 - val_loss: 0.0833 - val_mean_squared_error: 0.0833
Epoch 137/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1170 - mean_squared_error: 0.1170
Epoch 00137: val_loss did not improve from 0.08180
182/182 [==============================] - 0s 49us/sample - loss: 0.0930 - mean_squared_error: 0.0930 - val_loss: 0.0833 - val_mean_squared_error: 0.0833
Epoch 138/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0495 - mean_squared_error: 0.0495
Epoch 00138: val_loss improved from 0.08180 to 0.08169, saving model to model.h5
182/182 [==============================] - 0s 149us/sample - loss: 0.0838 - mean_squared_error: 0.0838 - val_loss: 0.0817 - val_mean_squared_error: 0.0817
Epoch 139/1000
 96/182 [

Epoch 162/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0670 - mean_squared_error: 0.0670
Epoch 00162: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 39us/sample - loss: 0.0765 - mean_squared_error: 0.0765 - val_loss: 0.0827 - val_mean_squared_error: 0.0827
Epoch 163/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0635 - mean_squared_error: 0.0635
Epoch 00163: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 42us/sample - loss: 0.0772 - mean_squared_error: 0.0772 - val_loss: 0.0829 - val_mean_squared_error: 0.0829
Epoch 164/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0946 - mean_squared_error: 0.0946
Epoch 00164: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 38us/sample - loss: 0.0725 - mean_squared_error: 0.0725 - val_loss: 0.0839 - val_mean_squared_error: 0.0839
Epoch 165/1000
 96/182 [==============>...............]

 96/182 [==============>...............] - ETA: 0s - loss: 0.1064 - mean_squared_error: 0.1064
Epoch 00188: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 38us/sample - loss: 0.0859 - mean_squared_error: 0.0859 - val_loss: 0.0841 - val_mean_squared_error: 0.0841
Epoch 189/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0922 - mean_squared_error: 0.0922
Epoch 00189: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 44us/sample - loss: 0.0757 - mean_squared_error: 0.0757 - val_loss: 0.0845 - val_mean_squared_error: 0.0845
Epoch 190/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0872 - mean_squared_error: 0.0872
Epoch 00190: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 38us/sample - loss: 0.0744 - mean_squared_error: 0.0744 - val_loss: 0.0841 - val_mean_squared_error: 0.0841
Epoch 191/1000
 96/182 [==============>...............] - ETA: 0s - lo

 96/182 [==============>...............] - ETA: 0s - loss: 0.0627 - mean_squared_error: 0.0627
Epoch 00214: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 38us/sample - loss: 0.0727 - mean_squared_error: 0.0727 - val_loss: 0.0867 - val_mean_squared_error: 0.0867
Epoch 215/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0874 - mean_squared_error: 0.0874
Epoch 00215: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 44us/sample - loss: 0.0763 - mean_squared_error: 0.0763 - val_loss: 0.0870 - val_mean_squared_error: 0.0870
Epoch 216/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0402 - mean_squared_error: 0.0402
Epoch 00216: val_loss did not improve from 0.08169
182/182 [==============================] - 0s 38us/sample - loss: 0.0707 - mean_squared_error: 0.0707 - val_loss: 0.0858 - val_mean_squared_error: 0.0858
Epoch 217/1000
 96/182 [==============>...............] - ETA: 0s - lo

In [15]:
lstm_r2_new = ave(lstm_ave_r2)
lstm_mse_new = ave(lstm_ave_mse)
lstm_ave_r2

[0.5441879464876852,
 0.5134854954974895,
 0.4945854505980566,
 0.5644522070710494,
 0.5122685550264898,
 0.573410366426093,
 0.46011313330036463,
 0.4900316507968967,
 0.5118342005659415,
 0.29440237913960743]

## GRU

In [16]:
test_pred_gru  = []

for fold in range(trials):
    print(f'Running trial {fold+1}')
    print(X_train.shape)
    
    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))
   

    check = ModelCheckpoint('model.h5', verbose=1, save_best_only=True)

    early = EarlyStopping(patience=100)

    optimizer = Adam(lr=0.00001)
    model = Sequential()
    model.add(GRU(50, input_shape=(1, 6)))
    model.add(Dropout(0.1))

    model.add(Dense(1))

    model.compile(loss='mse', optimizer='Adam', metrics=['mse'])

    

    history = model.fit(X_t_reshaped, 
                    y_train, 
                    validation_split = 0.2,
                    epochs=1000, 
                    batch_size=128, 
                    verbose=1, callbacks=[check, early])
    X_val_reshaped = X_val_reshaped.reshape(X_test.shape[0], 6)

    #running function
    test_forecast = X_test
    y_gru = forecast(model, test_forecast, gwl, steps_ahead)
    y_gru = np.array(y_gru)
    
    #metrics for test
    test_pred_gru.append(y_gru)
    mse_gru = mean_squared_error(y_test, y_gru)
    r2_gru = r2_score(y_test, y_gru)
    gru_ave_r2.append(r2_gru)
    gru_ave_mse.append(mse_gru)
    

Running trial 1
(228, 6)
Train on 182 samples, validate on 46 samples
Epoch 1/1000
128/182 [====================>.........] - ETA: 0s - loss: 1.0574 - mean_squared_error: 1.0574
Epoch 00001: val_loss improved from inf to 0.60994, saving model to model.h5
182/182 [==============================] - 1s 7ms/sample - loss: 1.1155 - mean_squared_error: 1.1155 - val_loss: 0.6099 - val_mean_squared_error: 0.6099
Epoch 2/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.8068 - mean_squared_error: 0.8068
Epoch 00002: val_loss improved from 0.60994 to 0.58911, saving model to model.h5
182/182 [==============================] - 0s 156us/sample - loss: 1.0140 - mean_squared_error: 1.0140 - val_loss: 0.5891 - val_mean_squared_error: 0.5891
Epoch 3/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.9880 - mean_squared_error: 0.9880
Epoch 00003: val_loss improved from 0.58911 to 0.56874, saving model to model.h5
182/182 [==============================] - 0s 152us/sample 

Epoch 25/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1782 - mean_squared_error: 0.1782
Epoch 00025: val_loss improved from 0.19165 to 0.17835, saving model to model.h5
182/182 [==============================] - 0s 156us/sample - loss: 0.1765 - mean_squared_error: 0.1765 - val_loss: 0.1784 - val_mean_squared_error: 0.1784
Epoch 26/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1477 - mean_squared_error: 0.1477
Epoch 00026: val_loss improved from 0.17835 to 0.16615, saving model to model.h5
182/182 [==============================] - 0s 157us/sample - loss: 0.1770 - mean_squared_error: 0.1770 - val_loss: 0.1662 - val_mean_squared_error: 0.1662
Epoch 27/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1874 - mean_squared_error: 0.1874
Epoch 00027: val_loss improved from 0.16615 to 0.15499, saving model to model.h5
182/182 [==============================] - 0s 154us/sample - loss: 0.1663 - mean_squared_error: 0.1663 - val_loss: 0.155

Epoch 49/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.0879 - mean_squared_error: 0.0879
Epoch 00049: val_loss improved from 0.08138 to 0.08113, saving model to model.h5
182/182 [==============================] - 0s 164us/sample - loss: 0.1249 - mean_squared_error: 0.1249 - val_loss: 0.0811 - val_mean_squared_error: 0.0811
Epoch 50/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1221 - mean_squared_error: 0.1221
Epoch 00050: val_loss improved from 0.08113 to 0.08095, saving model to model.h5
182/182 [==============================] - 0s 154us/sample - loss: 0.1189 - mean_squared_error: 0.1189 - val_loss: 0.0810 - val_mean_squared_error: 0.0810
Epoch 51/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.0731 - mean_squared_error: 0.0731
Epoch 00051: val_loss improved from 0.08095 to 0.08086, saving model to model.h5
182/182 [==============================] - 0s 155us/sample - loss: 0.1165 - mean_squared_error: 0.1165 - val_loss: 0.080

Epoch 75/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1218 - mean_squared_error: 0.1218
Epoch 00075: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 49us/sample - loss: 0.1162 - mean_squared_error: 0.1162 - val_loss: 0.0820 - val_mean_squared_error: 0.0820
Epoch 76/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1201 - mean_squared_error: 0.1201
Epoch 00076: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 44us/sample - loss: 0.1134 - mean_squared_error: 0.1134 - val_loss: 0.0821 - val_mean_squared_error: 0.0821
Epoch 77/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1385 - mean_squared_error: 0.1385
Epoch 00077: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 55us/sample - loss: 0.1239 - mean_squared_error: 0.1239 - val_loss: 0.0822 - val_mean_squared_error: 0.0822
Epoch 78/1000
128/182 [====================>.........] - E

128/182 [====================>.........] - ETA: 0s - loss: 0.1045 - mean_squared_error: 0.1045
Epoch 00101: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 44us/sample - loss: 0.1113 - mean_squared_error: 0.1113 - val_loss: 0.0839 - val_mean_squared_error: 0.0839
Epoch 102/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1104 - mean_squared_error: 0.1104
Epoch 00102: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 38us/sample - loss: 0.1042 - mean_squared_error: 0.1042 - val_loss: 0.0841 - val_mean_squared_error: 0.0841
Epoch 103/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1067 - mean_squared_error: 0.1067
Epoch 00103: val_loss did not improve from 0.08081
182/182 [==============================] - 0s 38us/sample - loss: 0.1074 - mean_squared_error: 0.1074 - val_loss: 0.0842 - val_mean_squared_error: 0.0842
Epoch 104/1000
128/182 [====================>.........] - ETA: 0s - lo

...

Epoch 31/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1612 - mean_squared_error: 0.1612
Epoch 00031: val_loss improved from 0.11983 to 0.11389, saving model to model.h5
182/182 [==============================] - 0s 202us/sample - loss: 0.1362 - mean_squared_error: 0.1362 - val_loss: 0.1139 - val_mean_squared_error: 0.1139
Epoch 32/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1347 - mean_squared_error: 0.1347
Epoch 00032: val_loss improved from 0.11389 to 0.10863, saving model to model.h5
182/182 [==============================] - 0s 181us/sample - loss: 0.1193 - mean_squared_error: 0.1193 - val_loss: 0.1086 - val_mean_squared_error: 0.1086
Epoch 33/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1099 - mean_squared_error: 0.1099
Epoch 00033: val_loss improved from 0.10863 to 0.10416, saving model to model.h5
182/182 [==============================] - 0s 242us/sample - loss: 0.1316 - mean_squared_error: 0.1316 - val_loss: 0.104

Epoch 55/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1334 - mean_squared_error: 0.1334
Epoch 00055: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 60us/sample - loss: 0.1208 - mean_squared_error: 0.1208 - val_loss: 0.0820 - val_mean_squared_error: 0.0820
Epoch 56/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.0961 - mean_squared_error: 0.0961
Epoch 00056: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 49us/sample - loss: 0.1157 - mean_squared_error: 0.1157 - val_loss: 0.0821 - val_mean_squared_error: 0.0821
Epoch 57/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1489 - mean_squared_error: 0.1489
Epoch 00057: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 63us/sample - loss: 0.1217 - mean_squared_error: 0.1217 - val_loss: 0.0821 - val_mean_squared_error: 0.0821
Epoch 58/1000
128/182 [====================>.........] - E

128/182 [====================>.........] - ETA: 0s - loss: 0.1045 - mean_squared_error: 0.1045
Epoch 00081: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 44us/sample - loss: 0.1002 - mean_squared_error: 0.1002 - val_loss: 0.0846 - val_mean_squared_error: 0.0846
Epoch 82/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1024 - mean_squared_error: 0.1024
Epoch 00082: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 102us/sample - loss: 0.1142 - mean_squared_error: 0.1142 - val_loss: 0.0846 - val_mean_squared_error: 0.0846
Epoch 83/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1126 - mean_squared_error: 0.1126
Epoch 00083: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 93us/sample - loss: 0.1077 - mean_squared_error: 0.1077 - val_loss: 0.0847 - val_mean_squared_error: 0.0847
Epoch 84/1000
128/182 [====================>.........] - ETA: 0s - loss

128/182 [====================>.........] - ETA: 0s - loss: 0.1130 - mean_squared_error: 0.1130
Epoch 00107: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 49us/sample - loss: 0.1117 - mean_squared_error: 0.1117 - val_loss: 0.0852 - val_mean_squared_error: 0.0852
Epoch 108/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.0974 - mean_squared_error: 0.0974
Epoch 00108: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 71us/sample - loss: 0.1092 - mean_squared_error: 0.1092 - val_loss: 0.0852 - val_mean_squared_error: 0.0852
Epoch 109/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1219 - mean_squared_error: 0.1219
Epoch 00109: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 60us/sample - loss: 0.1017 - mean_squared_error: 0.1017 - val_loss: 0.0853 - val_mean_squared_error: 0.0853
Epoch 110/1000
128/182 [====================>.........] - ETA: 0s - lo

128/182 [====================>.........] - ETA: 0s - loss: 0.0709 - mean_squared_error: 0.0709
Epoch 00133: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 55us/sample - loss: 0.0910 - mean_squared_error: 0.0910 - val_loss: 0.0849 - val_mean_squared_error: 0.0849
Epoch 134/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.0789 - mean_squared_error: 0.0789
Epoch 00134: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 55us/sample - loss: 0.0977 - mean_squared_error: 0.0977 - val_loss: 0.0849 - val_mean_squared_error: 0.0849
Epoch 135/1000
128/182 [====================>.........] - ETA: 0s - loss: 0.1035 - mean_squared_error: 0.1035
Epoch 00135: val_loss did not improve from 0.08174
182/182 [==============================] - 0s 71us/sample - loss: 0.0978 - mean_squared_error: 0.0978 - val_loss: 0.0848 - val_mean_squared_error: 0.0848
Epoch 136/1000
128/182 [====================>.........] - ETA: 0s - lo

In [17]:
gru_r2_new = ave(gru_ave_r2)
gru_mse_new = ave(gru_ave_mse)
gru_ave_r2
X_test.shape

(45, 6)

## FFNN

In [18]:
# X_test.shape
test_pred_ffnn  = []

for fold in range(trials):
    print(f'Running fold {fold}')
    print(X_train.shape)


    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))
    
    check = ModelCheckpoint('model.h5', verbose=1, save_best_only=True)

    early = EarlyStopping(patience=100)

    # Add fully connected layer with a ReLU activation function
    model.add(Dense(units=32, activation='relu', input_shape=(X_t_reshaped.shape[1], X_t_reshaped.shape[2])))

    # Add fully connected layer with a ReLU activation function
    model.add(Dense(units=32, activation='relu'))

    # Add fully connected layer with no activation function
    model.add(Dense(units=1))
    #model.add(Flatten())

    # Compile neural network
    model.compile(loss='mse', optimizer='rmsprop', metrics=['mse'])
    history = model.fit(X_t_reshaped, 
                    y_train, 
                    validation_split = 0.2,
                    epochs=1000, 
                    batch_size=96, 
                    verbose=1, callbacks=[check, early])
    

    #running function
    test_forecast = X_test
    y_ff = forecast(model, test_forecast, gwl, steps_ahead)
    y_ff = np.array(y_ff)
    
     #metrics for test
    test_pred_ffnn.append(y_ff)
    mse_ff = mean_squared_error(y_test, y_ff)
    r2_ff = r2_score(y_test, y_ff)
    ffnn_ave_r2.append(r2_ff)
    ffnn_ave_mse.append(mse_ff)
      

Running fold 0
(228, 6)
Train on 182 samples, validate on 46 samples
Epoch 1/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.1348 - mean_squared_error: 1.1348
Epoch 00001: val_loss improved from inf to 0.84550, saving model to model.h5
182/182 [==============================] - 2s 14ms/sample - loss: 1.1464 - mean_squared_error: 1.1464 - val_loss: 0.8455 - val_mean_squared_error: 0.8455
Epoch 2/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9465 - mean_squared_error: 0.9465
Epoch 00002: val_loss improved from 0.84550 to 0.77161, saving model to model.h5
182/182 [==============================] - 0s 218us/sample - loss: 1.0036 - mean_squared_error: 1.0036 - val_loss: 0.7716 - val_mean_squared_error: 0.7716
Epoch 3/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9949 - mean_squared_error: 0.9949
Epoch 00003: val_loss improved from 0.77161 to 0.69930, saving model to model.h5
182/182 [==============================] - 0s 214us/sample 

Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0944 - mean_squared_error: 0.0944
Epoch 00025: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 55us/sample - loss: 0.1153 - mean_squared_error: 0.1153 - val_loss: 0.0769 - val_mean_squared_error: 0.0769
Epoch 26/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0930 - mean_squared_error: 0.0930
Epoch 00026: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 71us/sample - loss: 0.1175 - mean_squared_error: 0.1175 - val_loss: 0.0767 - val_mean_squared_error: 0.0767
Epoch 27/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0698 - mean_squared_error: 0.0698
Epoch 00027: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 66us/sample - loss: 0.1190 - mean_squared_error: 0.1190 - val_loss: 0.0770 - val_mean_squared_error: 0.0770
Epoch 28/1000
 96/182 [==============>...............] - E

 96/182 [==============>...............] - ETA: 0s - loss: 0.1128 - mean_squared_error: 0.1128
Epoch 00051: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 60us/sample - loss: 0.0950 - mean_squared_error: 0.0950 - val_loss: 0.0803 - val_mean_squared_error: 0.0803
Epoch 52/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0735 - mean_squared_error: 0.0735
Epoch 00052: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 60us/sample - loss: 0.0900 - mean_squared_error: 0.0900 - val_loss: 0.0796 - val_mean_squared_error: 0.0796
Epoch 53/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0641 - mean_squared_error: 0.0641
Epoch 00053: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 60us/sample - loss: 0.0876 - mean_squared_error: 0.0876 - val_loss: 0.0791 - val_mean_squared_error: 0.0791
Epoch 54/1000
 96/182 [==============>...............] - ETA: 0s - loss:

 96/182 [==============>...............] - ETA: 0s - loss: 0.0581 - mean_squared_error: 0.0581
Epoch 00077: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 49us/sample - loss: 0.0797 - mean_squared_error: 0.0797 - val_loss: 0.0808 - val_mean_squared_error: 0.0808
Epoch 78/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0685 - mean_squared_error: 0.0685
Epoch 00078: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 48us/sample - loss: 0.0817 - mean_squared_error: 0.0817 - val_loss: 0.0809 - val_mean_squared_error: 0.0809
Epoch 79/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0793 - mean_squared_error: 0.0793
Epoch 00079: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 61us/sample - loss: 0.0891 - mean_squared_error: 0.0891 - val_loss: 0.0814 - val_mean_squared_error: 0.0814
Epoch 80/1000
 96/182 [==============>...............] - ETA: 0s - loss:

 96/182 [==============>...............] - ETA: 0s - loss: 0.0548 - mean_squared_error: 0.0548
Epoch 00103: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 60us/sample - loss: 0.0765 - mean_squared_error: 0.0765 - val_loss: 0.0821 - val_mean_squared_error: 0.0821
Epoch 104/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0969 - mean_squared_error: 0.0969
Epoch 00104: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 49us/sample - loss: 0.0748 - mean_squared_error: 0.0748 - val_loss: 0.0838 - val_mean_squared_error: 0.0838
Epoch 105/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0442 - mean_squared_error: 0.0442
Epoch 00105: val_loss did not improve from 0.07627
182/182 [==============================] - 0s 55us/sample - loss: 0.0710 - mean_squared_error: 0.0710 - val_loss: 0.0823 - val_mean_squared_error: 0.0823
Epoch 106/1000
 96/182 [==============>...............] - ETA: 0s - lo

...

 96/182 [==============>...............] - ETA: 0s - loss: 0.0850 - mean_squared_error: 0.0850
Epoch 00104: val_loss did not improve from 0.08101
182/182 [==============================] - 0s 98us/sample - loss: 0.1197 - mean_squared_error: 0.1197 - val_loss: 0.0877 - val_mean_squared_error: 0.0877
Epoch 105/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0934 - mean_squared_error: 0.0934
Epoch 00105: val_loss did not improve from 0.08101
182/182 [==============================] - 0s 77us/sample - loss: 0.0698 - mean_squared_error: 0.0698 - val_loss: 0.0984 - val_mean_squared_error: 0.0984
Epoch 106/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0873 - mean_squared_error: 0.0873
Epoch 00106: val_loss did not improve from 0.08101
182/182 [==============================] - 0s 82us/sample - loss: 0.0714 - mean_squared_error: 0.0714 - val_loss: 0.0988 - val_mean_squared_error: 0.0988
Epoch 107/1000
 96/182 [==============>...............] - ETA: 0s - lo

Epoch 23/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0975 - mean_squared_error: 0.0975
Epoch 00023: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 99us/sample - loss: 0.0651 - mean_squared_error: 0.0651 - val_loss: 0.0834 - val_mean_squared_error: 0.0834
Epoch 24/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0472 - mean_squared_error: 0.0472
Epoch 00024: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 88us/sample - loss: 0.0690 - mean_squared_error: 0.0690 - val_loss: 0.0830 - val_mean_squared_error: 0.0830
Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0755 - mean_squared_error: 0.0755
Epoch 00025: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 93us/sample - loss: 0.0711 - mean_squared_error: 0.0711 - val_loss: 0.0847 - val_mean_squared_error: 0.0847
Epoch 26/1000
 96/182 [==============>...............] - E

 96/182 [==============>...............] - ETA: 0s - loss: 0.0828 - mean_squared_error: 0.0828
Epoch 00049: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 82us/sample - loss: 0.0818 - mean_squared_error: 0.0818 - val_loss: 0.0836 - val_mean_squared_error: 0.0836
Epoch 50/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1014 - mean_squared_error: 0.1014
Epoch 00050: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 76us/sample - loss: 0.0880 - mean_squared_error: 0.0880 - val_loss: 0.0839 - val_mean_squared_error: 0.0839
Epoch 51/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1376 - mean_squared_error: 0.1376
Epoch 00051: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 88us/sample - loss: 0.1112 - mean_squared_error: 0.1112 - val_loss: 0.0836 - val_mean_squared_error: 0.0836
Epoch 52/1000
 96/182 [==============>...............] - ETA: 0s - loss:

 96/182 [==============>...............] - ETA: 0s - loss: 0.0820 - mean_squared_error: 0.0820
Epoch 00075: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 99us/sample - loss: 0.0655 - mean_squared_error: 0.0655 - val_loss: 0.1033 - val_mean_squared_error: 0.1033
Epoch 76/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0787 - mean_squared_error: 0.0787
Epoch 00076: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 82us/sample - loss: 0.0622 - mean_squared_error: 0.0622 - val_loss: 0.0839 - val_mean_squared_error: 0.0839
Epoch 77/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0268 - mean_squared_error: 0.0268
Epoch 00077: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 88us/sample - loss: 0.0650 - mean_squared_error: 0.0650 - val_loss: 0.0838 - val_mean_squared_error: 0.0838
Epoch 78/1000
 96/182 [==============>...............] - ETA: 0s - loss:

 96/182 [==============>...............] - ETA: 0s - loss: 0.0821 - mean_squared_error: 0.0821
Epoch 00101: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 82us/sample - loss: 0.0747 - mean_squared_error: 0.0747 - val_loss: 0.1220 - val_mean_squared_error: 0.1220
Epoch 102/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0660 - mean_squared_error: 0.0660
Epoch 00102: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 77us/sample - loss: 0.0792 - mean_squared_error: 0.0792 - val_loss: 0.1310 - val_mean_squared_error: 0.1310
Epoch 103/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0900 - mean_squared_error: 0.0900
Epoch 00103: val_loss did not improve from 0.08137
182/182 [==============================] - 0s 93us/sample - loss: 0.0694 - mean_squared_error: 0.0694 - val_loss: 0.1156 - val_mean_squared_error: 0.1156


In [19]:
ffnn_r2_new = ave(ffnn_ave_r2)
ffnn_mse_new = ave(ffnn_ave_mse)
ffnn_ave_r2

[0.5249474948234423,
 0.5513327502908443,
 0.4646192649871499,
 0.4450153226219209,
 0.37316448141842173,
 0.009087699421091555,
 0.3743088828930843,
 0.4627014291056445,
 -0.45898933611697523,
 -0.14814087108100926]

## LSTM-GRU

In [20]:
test_pred_lstm_gru  = []


for fold in range(trials):
    print(f'Running trial {fold+1}')
    print(X_train.shape)
    
    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))


    check = ModelCheckpoint('model.h5', verbose=1, save_best_only=True)

    early = EarlyStopping(patience=100)

    optimizer = Adam(lr=0.00001)
    model = Sequential()
    model.add(GRU(50,return_sequences= True, input_shape=(X_t_reshaped.shape[1], X_t_reshaped.shape[2])))
    model.add(Dropout(0.1))
    model.add(LSTM(50,return_sequences= False))
    model.add(Dropout(0.1))

    model.add(Dense(1))
    
# validation_split = 0.2
    model.compile(loss='mse', optimizer='Adam', metrics=['mse'])

    

    history = model.fit(X_t_reshaped, 
                    y_train, 
                    validation_split = 0.2,
                    epochs=1000, 
                    batch_size=96, 
                    verbose=1, callbacks=[check, early])
    X_val_reshaped = X_val_reshaped.reshape(X_test.shape[0], 6)

    #running function
    test_forecast = X_test
    y_lstm_gru = forecast(model, test_forecast, gwl, steps_ahead)
    y_lstm_gru = np.array(y_lstm_gru)
    
    #metrics for test
    test_pred_lstm_gru.append(y_lstm_gru)
    mse_lstm_gru = mean_squared_error(y_test, y_lstm_gru)
    r2_lstm_gru = r2_score(y_test, y_lstm_gru)
    lstm_gru_ave_r2.append(r2_lstm_gru)
    lstm_gru_ave_mse.append(mse_lstm_gru)
    

Running trial 1
(228, 6)
Train on 182 samples, validate on 46 samples
Epoch 1/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.0622 - mean_squared_error: 1.0622
Epoch 00001: val_loss improved from inf to 0.72399, saving model to model.h5
182/182 [==============================] - 5s 27ms/sample - loss: 1.2114 - mean_squared_error: 1.2114 - val_loss: 0.7240 - val_mean_squared_error: 0.7240
Epoch 2/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.1319 - mean_squared_error: 1.1319
Epoch 00002: val_loss improved from 0.72399 to 0.70922, saving model to model.h5
182/182 [==============================] - 0s 305us/sample - loss: 1.1530 - mean_squared_error: 1.1530 - val_loss: 0.7092 - val_mean_squared_error: 0.7092
Epoch 3/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.0299 - mean_squared_error: 1.0299
Epoch 00003: val_loss improved from 0.70922 to 0.69428, saving model to model.h5
182/182 [==============================] - 0s 292us/sample

Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.2058 - mean_squared_error: 0.2058
Epoch 00025: val_loss improved from 0.26999 to 0.25293, saving model to model.h5
182/182 [==============================] - 0s 248us/sample - loss: 0.1992 - mean_squared_error: 0.1992 - val_loss: 0.2529 - val_mean_squared_error: 0.2529
Epoch 26/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.2003 - mean_squared_error: 0.2003
Epoch 00026: val_loss improved from 0.25293 to 0.23830, saving model to model.h5
182/182 [==============================] - 0s 247us/sample - loss: 0.1846 - mean_squared_error: 0.1846 - val_loss: 0.2383 - val_mean_squared_error: 0.2383
Epoch 27/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.2219 - mean_squared_error: 0.2219
Epoch 00027: val_loss improved from 0.23830 to 0.22598, saving model to model.h5
182/182 [==============================] - 0s 249us/sample - loss: 0.1866 - mean_squared_error: 0.1866 - val_loss: 0.226

Epoch 49/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1264 - mean_squared_error: 0.1264
Epoch 00049: val_loss improved from 0.10638 to 0.10489, saving model to model.h5
182/182 [==============================] - 0s 241us/sample - loss: 0.1210 - mean_squared_error: 0.1210 - val_loss: 0.1049 - val_mean_squared_error: 0.1049
Epoch 50/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0894 - mean_squared_error: 0.0894
Epoch 00050: val_loss improved from 0.10489 to 0.10360, saving model to model.h5
182/182 [==============================] - 0s 219us/sample - loss: 0.1373 - mean_squared_error: 0.1373 - val_loss: 0.1036 - val_mean_squared_error: 0.1036
Epoch 51/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1665 - mean_squared_error: 0.1665
Epoch 00051: val_loss improved from 0.10360 to 0.10264, saving model to model.h5
182/182 [==============================] - 0s 275us/sample - loss: 0.1269 - mean_squared_error: 0.1269 - val_loss: 0.102

Epoch 73/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1141 - mean_squared_error: 0.1141
Epoch 00073: val_loss improved from 0.09563 to 0.09530, saving model to model.h5
182/182 [==============================] - 0s 329us/sample - loss: 0.1056 - mean_squared_error: 0.1056 - val_loss: 0.0953 - val_mean_squared_error: 0.0953
Epoch 74/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1010 - mean_squared_error: 0.1010
Epoch 00074: val_loss improved from 0.09530 to 0.09500, saving model to model.h5
182/182 [==============================] - 0s 245us/sample - loss: 0.1122 - mean_squared_error: 0.1122 - val_loss: 0.0950 - val_mean_squared_error: 0.0950
Epoch 75/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1468 - mean_squared_error: 0.1468
Epoch 00075: val_loss improved from 0.09500 to 0.09465, saving model to model.h5
182/182 [==============================] - 0s 393us/sample - loss: 0.1232 - mean_squared_error: 0.1232 - val_loss: 0.094

Epoch 97/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1434 - mean_squared_error: 0.1434
Epoch 00097: val_loss did not improve from 0.08919
182/182 [==============================] - 0s 110us/sample - loss: 0.1030 - mean_squared_error: 0.1030 - val_loss: 0.0893 - val_mean_squared_error: 0.0893
Epoch 98/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0894 - mean_squared_error: 0.0894
Epoch 00098: val_loss did not improve from 0.08919
182/182 [==============================] - 0s 87us/sample - loss: 0.1106 - mean_squared_error: 0.1106 - val_loss: 0.0893 - val_mean_squared_error: 0.0893
Epoch 99/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1127 - mean_squared_error: 0.1127
Epoch 00099: val_loss improved from 0.08919 to 0.08900, saving model to model.h5
182/182 [==============================] - 0s 275us/sample - loss: 0.1059 - mean_squared_error: 0.1059 - val_loss: 0.0890 - val_mean_squared_error: 0.0890
Epoch 100/1000
 96/182 [==

...

Epoch 201/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0986 - mean_squared_error: 0.0986
Epoch 00201: val_loss did not improve from 0.08076
182/182 [==============================] - 0s 54us/sample - loss: 0.0780 - mean_squared_error: 0.0780 - val_loss: 0.0818 - val_mean_squared_error: 0.0818
Epoch 202/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0582 - mean_squared_error: 0.0582
Epoch 00202: val_loss did not improve from 0.08076
182/182 [==============================] - 0s 110us/sample - loss: 0.0780 - mean_squared_error: 0.0780 - val_loss: 0.0829 - val_mean_squared_error: 0.0829
Epoch 203/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0647 - mean_squared_error: 0.0647
Epoch 00203: val_loss did not improve from 0.08076
182/182 [==============================] - 0s 110us/sample - loss: 0.0758 - mean_squared_error: 0.0758 - val_loss: 0.0839 - val_mean_squared_error: 0.0839
Epoch 204/1000
 96/182 [==============>..............

Epoch 227/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0675 - mean_squared_error: 0.0675
Epoch 00227: val_loss improved from 0.07988 to 0.07978, saving model to model.h5
182/182 [==============================] - 0s 273us/sample - loss: 0.0835 - mean_squared_error: 0.0835 - val_loss: 0.0798 - val_mean_squared_error: 0.0798
Epoch 228/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0695 - mean_squared_error: 0.0695
Epoch 00228: val_loss improved from 0.07978 to 0.07977, saving model to model.h5
182/182 [==============================] - 0s 276us/sample - loss: 0.0787 - mean_squared_error: 0.0787 - val_loss: 0.0798 - val_mean_squared_error: 0.0798
Epoch 229/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1028 - mean_squared_error: 0.1028
Epoch 00229: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 71us/sample - loss: 0.0759 - mean_squared_error: 0.0759 - val_loss: 0.0802 - val_mean_squared_error: 

Epoch 253/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0870 - mean_squared_error: 0.0870
Epoch 00253: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 110us/sample - loss: 0.0732 - mean_squared_error: 0.0732 - val_loss: 0.0822 - val_mean_squared_error: 0.0822
Epoch 254/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1060 - mean_squared_error: 0.1060
Epoch 00254: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 109us/sample - loss: 0.0754 - mean_squared_error: 0.0754 - val_loss: 0.0825 - val_mean_squared_error: 0.0825
Epoch 255/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0918 - mean_squared_error: 0.0918
Epoch 00255: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 109us/sample - loss: 0.0702 - mean_squared_error: 0.0702 - val_loss: 0.0825 - val_mean_squared_error: 0.0825
Epoch 256/1000
 96/182 [==============>.............

Epoch 279/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0868 - mean_squared_error: 0.0868
Epoch 00279: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 55us/sample - loss: 0.0735 - mean_squared_error: 0.0735 - val_loss: 0.0833 - val_mean_squared_error: 0.0833
Epoch 280/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0412 - mean_squared_error: 0.0412
Epoch 00280: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 110us/sample - loss: 0.0720 - mean_squared_error: 0.0720 - val_loss: 0.0837 - val_mean_squared_error: 0.0837
Epoch 281/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1005 - mean_squared_error: 0.1005
Epoch 00281: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 109us/sample - loss: 0.0763 - mean_squared_error: 0.0763 - val_loss: 0.0834 - val_mean_squared_error: 0.0834
Epoch 282/1000
 96/182 [==============>..............

Epoch 305/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0850 - mean_squared_error: 0.0850
Epoch 00305: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 109us/sample - loss: 0.0727 - mean_squared_error: 0.0727 - val_loss: 0.0827 - val_mean_squared_error: 0.0827
Epoch 306/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0440 - mean_squared_error: 0.0440
Epoch 00306: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 56us/sample - loss: 0.0691 - mean_squared_error: 0.0691 - val_loss: 0.0835 - val_mean_squared_error: 0.0835
Epoch 307/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0479 - mean_squared_error: 0.0479
Epoch 00307: val_loss did not improve from 0.07977
182/182 [==============================] - 0s 55us/sample - loss: 0.0731 - mean_squared_error: 0.0731 - val_loss: 0.0838 - val_mean_squared_error: 0.0838
Epoch 308/1000
 96/182 [==============>...............

In [21]:
lstm_gru_r2_new = ave(lstm_gru_ave_r2)
lstm_gru_mse_new = ave(lstm_gru_ave_mse)
lstm_gru_ave_r2

[0.5785947856404692,
 0.6349716159436316,
 0.5769055522768765,
 0.4446652331730291,
 0.5895008625692371,
 0.27601828208031964,
 0.5666163292547113,
 0.6127779362943269,
 0.5665803000471731,
 0.5866618943484639]

## DBN-LSTM

In [22]:
Y = Y.reshape(-1,1)
tss = TimeSeriesSplit(n_splits = 5)
for train_index, test_index in tss.split(X):
    X_train, X_test = X[train_index, :], X[test_index,:]
    y_train, y_test = Y[train_index], Y[test_index]
    

dummyXtrain = pd.DataFrame(X_train)
dummyXtrain.columns = ['a','b','c','d','e','f', 'g']
X_train = np.array(dummyXtrain.drop(['g'], axis = 1).reset_index(drop=True))

dummyXtest = pd.DataFrame(X_test)
dummyXtest.columns = ['a','b','c','d','e','f', 'g']
X_test = np.array(dummyXtest.drop(['g'], axis = 1).reset_index(drop=True))

X_train = regress.transform(X_train)
X_test = regress.transform(X_test)

print (X_train.shape, y_train.shape)
print (X_test.shape, y_test.shape)

(228, 16) (228, 1)
(45, 16) (45, 1)


In [23]:
def forecast_hybrid(model, test_forecast, gwl, steps_ahead):
    y_pred = []
    current_output = gwl
    for step in range(steps_ahead):
        #print(test_forecast[step])
        input_test = np.concatenate([test_forecast[step][:-1], [current_output]])
        #input_test = [test_forecast[0][0][:-1], gwl]
        #print(input_test)
        pred = model.predict(input_test.reshape(1,1,X_test.shape[1]))
        y_pred.append(pred[0][0])
        #print(pred)
        current_output = pred[0][0]

    return y_pred

In [ ]:
# rounding off
Round = 3      

test_pred_dbn_lstm  = [] 

for fold in range(trials):
    print(f'Running trial {fold+1}')
    print(X_train.shape)
    
    X_t_reshaped   = X_train.reshape((X_train.shape[0], 1, X_train.shape[1]))
    X_val_reshaped = X_test.reshape((X_test.shape[0], 1, X_test.shape[1]))
    
    steps_ahead = X_test.shape[0]

    check = ModelCheckpoint('model.h5', verbose=1, save_best_only=True)

    early = EarlyStopping(patience=100)

    optimizer = Adam(lr=0.01)
    model = Sequential()
    model.add(LSTM(50, input_shape=(X_t_reshaped.shape[1], X_t_reshaped.shape[2])))
    model.add(Dropout(0.2))

    model.add(Dense(1))

    model.compile(loss='mse', optimizer='Adam', metrics=['mse'])

    

    history = model.fit(X_t_reshaped, 
                    y_train, 
                    validation_split = 0.2,
                    epochs=1000, 
                    batch_size=96, 
                    verbose=1, callbacks=[check, early])
    X_val_reshaped = X_val_reshaped.reshape(X_test.shape[0], X_test.shape[1])

    #running function
    test_forecast = X_test
    dbn_lstm_y = forecast_hybrid(model, test_forecast, gwl, steps_ahead)
    dbn_lstm_y = np.array(dbn_lstm_y)
    
    #metrics for test
    test_pred_dbn_lstm.append(dbn_lstm_y)
    mse_dbn_lstm = mean_squared_error(y_test, dbn_lstm_y)
    r2_dbn_lstm = r2_score(y_test, dbn_lstm_y)
    dbn_lstm_ave_r2.append(r2_dbn_lstm)
    dbn_lstm_ave_mse.append(mse_dbn_lstm)
    

Running trial 1
(228, 16)
Train on 182 samples, validate on 46 samples
Epoch 1/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.1551 - mean_squared_error: 1.1551
Epoch 00001: val_loss improved from inf to 0.74592, saving model to model.h5
182/182 [==============================] - 5s 29ms/sample - loss: 1.2096 - mean_squared_error: 1.2096 - val_loss: 0.7459 - val_mean_squared_error: 0.7459
Epoch 2/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.1999 - mean_squared_error: 1.1999
Epoch 00002: val_loss improved from 0.74592 to 0.71307, saving model to model.h5
182/182 [==============================] - 0s 251us/sample - loss: 1.1844 - mean_squared_error: 1.1844 - val_loss: 0.7131 - val_mean_squared_error: 0.7131
Epoch 3/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.2095 - mean_squared_error: 1.2095
Epoch 00003: val_loss improved from 0.71307 to 0.68130, saving model to model.h5
182/182 [==============================] - 0s 165us/sampl

Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.7235 - mean_squared_error: 0.7235
Epoch 00025: val_loss improved from 0.19641 to 0.18289, saving model to model.h5
182/182 [==============================] - 0s 221us/sample - loss: 0.8000 - mean_squared_error: 0.8000 - val_loss: 0.1829 - val_mean_squared_error: 0.1829
Epoch 26/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9616 - mean_squared_error: 0.9616
Epoch 00026: val_loss improved from 0.18289 to 0.17099, saving model to model.h5
182/182 [==============================] - 0s 275us/sample - loss: 0.7829 - mean_squared_error: 0.7829 - val_loss: 0.1710 - val_mean_squared_error: 0.1710
Epoch 27/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9292 - mean_squared_error: 0.9292
Epoch 00027: val_loss improved from 0.17099 to 0.16031, saving model to model.h5
182/182 [==============================] - 0s 221us/sample - loss: 0.7704 - mean_squared_error: 0.7704 - val_loss: 0.160

Epoch 49/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.3265 - mean_squared_error: 0.3265
Epoch 00049: val_loss improved from 0.08645 to 0.08548, saving model to model.h5
182/182 [==============================] - 0s 220us/sample - loss: 0.3745 - mean_squared_error: 0.3745 - val_loss: 0.0855 - val_mean_squared_error: 0.0855
Epoch 50/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.3823 - mean_squared_error: 0.3823
Epoch 00050: val_loss improved from 0.08548 to 0.08493, saving model to model.h5
182/182 [==============================] - 0s 212us/sample - loss: 0.3807 - mean_squared_error: 0.3807 - val_loss: 0.0849 - val_mean_squared_error: 0.0849
Epoch 51/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.3634 - mean_squared_error: 0.3634
Epoch 00051: val_loss improved from 0.08493 to 0.08461, saving model to model.h5
182/182 [==============================] - 0s 221us/sample - loss: 0.3613 - mean_squared_error: 0.3613 - val_loss: 0.084

Epoch 75/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1561 - mean_squared_error: 0.1561
Epoch 00075: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 41us/sample - loss: 0.1339 - mean_squared_error: 0.1339 - val_loss: 0.1230 - val_mean_squared_error: 0.1230
Epoch 76/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1819 - mean_squared_error: 0.1819
Epoch 00076: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 56us/sample - loss: 0.1368 - mean_squared_error: 0.1368 - val_loss: 0.1258 - val_mean_squared_error: 0.1258
Epoch 77/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1221 - mean_squared_error: 0.1221
Epoch 00077: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 55us/sample - loss: 0.1325 - mean_squared_error: 0.1325 - val_loss: 0.1284 - val_mean_squared_error: 0.1284
Epoch 78/1000
 96/182 [==============>...............] - E

 96/182 [==============>...............] - ETA: 0s - loss: 0.0810 - mean_squared_error: 0.0810
Epoch 00101: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 55us/sample - loss: 0.1071 - mean_squared_error: 0.1071 - val_loss: 0.1253 - val_mean_squared_error: 0.1253
Epoch 102/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1306 - mean_squared_error: 0.1306
Epoch 00102: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 111us/sample - loss: 0.1024 - mean_squared_error: 0.1024 - val_loss: 0.1236 - val_mean_squared_error: 0.1236
Epoch 103/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1212 - mean_squared_error: 0.1212
Epoch 00103: val_loss did not improve from 0.08453
182/182 [==============================] - 0s 55us/sample - loss: 0.0990 - mean_squared_error: 0.0990 - val_loss: 0.1206 - val_mean_squared_error: 0.1206
Epoch 104/1000
 96/182 [==============>...............] - ETA: 0s - l

...

Epoch 236/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0946 - mean_squared_error: 0.0946
Epoch 00236: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0881 - mean_squared_error: 0.0881 - val_loss: 0.0744 - val_mean_squared_error: 0.0744
Epoch 237/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1094 - mean_squared_error: 0.1094
Epoch 00237: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 118us/sample - loss: 0.0849 - mean_squared_error: 0.0849 - val_loss: 0.0744 - val_mean_squared_error: 0.0744
Epoch 238/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0670 - mean_squared_error: 0.0670
Epoch 00238: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 84us/sample - loss: 0.0851 - mean_squared_error: 0.0851 - val_loss: 0.0744 - val_mean_squared_error: 0.0744
Epoch 239/1000
 96/182 [==============>...............

Epoch 262/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1108 - mean_squared_error: 0.1108
Epoch 00262: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0809 - mean_squared_error: 0.0809 - val_loss: 0.0748 - val_mean_squared_error: 0.0748
Epoch 263/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0894 - mean_squared_error: 0.0894
Epoch 00263: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0893 - mean_squared_error: 0.0893 - val_loss: 0.0748 - val_mean_squared_error: 0.0748
Epoch 264/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0768 - mean_squared_error: 0.0768
Epoch 00264: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 116us/sample - loss: 0.0875 - mean_squared_error: 0.0875 - val_loss: 0.0748 - val_mean_squared_error: 0.0748
Epoch 265/1000
 96/182 [==============>...............

Epoch 288/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0696 - mean_squared_error: 0.0696
Epoch 00288: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 79us/sample - loss: 0.0771 - mean_squared_error: 0.0771 - val_loss: 0.0753 - val_mean_squared_error: 0.0753
Epoch 289/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0997 - mean_squared_error: 0.0997
Epoch 00289: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0810 - mean_squared_error: 0.0810 - val_loss: 0.0753 - val_mean_squared_error: 0.0753
Epoch 290/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.0883 - mean_squared_error: 0.0883
Epoch 00290: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0851 - mean_squared_error: 0.0851 - val_loss: 0.0754 - val_mean_squared_error: 0.0754
Epoch 291/1000
 96/182 [==============>...............]

Epoch 314/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.1040 - mean_squared_error: 0.1040
Epoch 00314: val_loss did not improve from 0.07416
182/182 [==============================] - 0s 77us/sample - loss: 0.0829 - mean_squared_error: 0.0829 - val_loss: 0.0759 - val_mean_squared_error: 0.0759
Running trial 10
(228, 16)
Train on 182 samples, validate on 46 samples
Epoch 1/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.1350 - mean_squared_error: 1.1350
Epoch 00001: val_loss improved from inf to 0.85756, saving model to model.h5
182/182 [==============================] - 6s 33ms/sample - loss: 1.2073 - mean_squared_error: 1.2073 - val_loss: 0.8576 - val_mean_squared_error: 0.8576
Epoch 2/1000
 96/182 [==============>...............] - ETA: 0s - loss: 1.0504 - mean_squared_error: 1.0504
Epoch 00002: val_loss improved from 0.85756 to 0.82137, saving model to model.h5
182/182 [==============================] - 0s 268us/sample - loss: 1.1942 - mean_squa

Epoch 24/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.9005 - mean_squared_error: 0.9005
Epoch 00024: val_loss improved from 0.27699 to 0.25908, saving model to model.h5
182/182 [==============================] - 0s 259us/sample - loss: 0.8340 - mean_squared_error: 0.8340 - val_loss: 0.2591 - val_mean_squared_error: 0.2591
Epoch 25/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.8076 - mean_squared_error: 0.8076
Epoch 00025: val_loss improved from 0.25908 to 0.24217, saving model to model.h5
182/182 [==============================] - 0s 286us/sample - loss: 0.8158 - mean_squared_error: 0.8158 - val_loss: 0.2422 - val_mean_squared_error: 0.2422
Epoch 26/1000
 96/182 [==============>...............] - ETA: 0s - loss: 0.6499 - mean_squared_error: 0.6499
Epoch 00026: val_loss improved from 0.24217 to 0.22639, saving model to model.h5
182/182 [==============================] - 0s 242us/sample - loss: 0.8021 - mean_squared_error: 0.8021 - val_loss: 0.226

In [ ]:
dbn_lstm_r2_new = ave(dbn_lstm_ave_r2)
dbn_lstm_mse_new = ave(dbn_lstm_ave_mse)
dbn_lstm_ave_r2

In [ ]:
def fix(year):
    s = year.split('-')
    new_year = s[0]
    return new_year

# dummyXtest['g']
df_train = dummyXtrain['g'].apply(lambda x : fix(x))
year_train = np.array(df_train.tolist())

df_test = dummyXtest['g'].apply(lambda x : fix(x))
year_test = np.array(df_test.tolist())
len(year_test)

In [ ]:
from operator import add
import statistics

def extract(lst):
    return [[el] for el in lst]

df_fake = df.copy()
n = len(test_pred_dbn_lstm[0])

pred_lstm = [0] * n
pred_gru = [0] * n
pred_ffnn = [0] * n
pred_lstm_gru = [0] * n
pred_dbn_lstm = [0] * n


for i in range(len(test_pred_dbn_lstm)):
    y_lstm = test_pred_lstm[i].tolist()
    y_gru = test_pred_gru[i].tolist()
    y_ffnn = test_pred_ffnn[i].tolist()
    y_lstm_gru = test_pred_lstm_gru[i].tolist()
    y_dbn_lstm = test_pred_dbn_lstm[i].tolist()
    
    pred_lstm = list( map(add, pred_lstm, y_lstm))
    pred_lstm_gru = list( map(add, pred_lstm_gru, y_lstm_gru))
    pred_dbn_lstm = list( map(add, pred_dbn_lstm, y_dbn_lstm))
    pred_gru = list( map(add, pred_gru, y_gru))
    pred_ffnn = list( map(add, pred_ffnn, y_ffnn))

    
y_pred_LSTM = []
y_pred_LSTM_GRU = []
y_pred_DBN_LSTM = []
y_pred_GRU = []
y_pred_FFNN = []

for i in range(len(pred_lstm)):
    ay_lstm = float(pred_lstm[i]/len(test_pred_lstm))
    ay_lstm_gru = float(pred_lstm_gru[i]/len(test_pred_lstm_gru))
    ay_dbn_lstm = float(pred_dbn_lstm[i]/len(test_pred_dbn_lstm))
    ay_gru = float(pred_gru[i]/len(test_pred_gru))
    ay_ffnn = float(pred_ffnn[i]/len(test_pred_ffnn))
    
    
    y_pred_LSTM.append(ay_lstm)
    y_pred_LSTM_GRU.append(ay_lstm_gru)
    y_pred_DBN_LSTM.append(ay_dbn_lstm)
    y_pred_GRU.append(ay_gru)
    y_pred_FFNN.append(ay_ffnn)
    

y_pred_LSTM = extract(y_pred_LSTM)
y_pred_LSTM_GRU = extract(y_pred_LSTM_GRU)
y_pred_DBN_LSTM = extract(y_pred_DBN_LSTM)
y_pred_FFNN = extract(y_pred_FFNN)
y_pred_GRU = extract(y_pred_GRU)

# Y_test = extract(Y_test)
# Y_train = extract(Y_train)


y_pred_LSTM = scalery.inverse_transform(y_pred_LSTM)*-1
y_pred_LSTM_GRU = scalery.inverse_transform(y_pred_LSTM_GRU)*-1
y_pred_DBN_LSTM = scalery.inverse_transform(y_pred_DBN_LSTM)*-1
y_pred_GRU = scalery.inverse_transform(y_pred_GRU)*-1
y_pred_FFNN = scalery.inverse_transform(y_pred_FFNN)*-1


# Y_test
# error = history.history['val_loss']
# error = scalery.inverse_transform(error)

Y_test_sc = scalery.inverse_transform(Y_test)*-1

Y_train_sc = scalery.inverse_transform(Y_train)*-1

# #LSTM
pred_LSTM = pd.DataFrame(y_pred_LSTM)
pred_LSTM['y'] = pd.DataFrame(year_test)
pred_LSTM.columns = ['LSTM_gwls', 'y']
pred_LSTM = pred_LSTM.set_index('y')

# #LSTM_GRU
pred_LSTM_GRU = pd.DataFrame(y_pred_LSTM_GRU)
pred_LSTM_GRU['y'] = pd.DataFrame(year_test)
pred_LSTM_GRU.columns = ['LSTM_GRU_gwls', 'y']
pred_LSTM_GRU = pred_LSTM_GRU.set_index('y')

#DBN-LSTM
y_pred_DBN_LSTM = pd.DataFrame(y_pred_DBN_LSTM)
y_pred_DBN_LSTM['y'] = pd.DataFrame(year_test)
y_pred_DBN_LSTM.columns = ['DBN_LSTM_gwls', 'y']
y_pred_DBN_LSTM = y_pred_DBN_LSTM.set_index('y')

#FFNN
pred_FFNN = pd.DataFrame(y_pred_FFNN)
pred_FFNN['y'] = pd.DataFrame(year_test)
pred_FFNN.columns = ['FFNN_gwls', 'y']
pred_FFNN = pred_FFNN.set_index('y')

#GRU
pred_GRU = pd.DataFrame(y_pred_GRU)
pred_GRU['y'] = pd.DataFrame(year_test)
pred_GRU.columns = ['GRU_gwls', 'y']
pred_GRU = pred_GRU.set_index('y')


real_output = pd.DataFrame(Y_test_sc)
real_output['y'] = pd.DataFrame(year_test)
real_output.columns = ['actual_test_gwls', 'y']
real_output = real_output.set_index('y')

train_output = pd.DataFrame(Y_train_sc)
train_output['y'] = pd.DataFrame(year_train)
train_output.columns = ['actual_gwls', 'y']
train_output = train_output.set_index('y')

pre_df = pd.concat([real_output, pred_LSTM,pred_GRU,pred_FFNN , pred_LSTM_GRU, y_pred_DBN_LSTM], axis = 1)

# the_df = pd.concat([train_output,pre_df], axis = 0)

mess_LSTM = pd.DataFrame(test_pred_lstm).transpose()
mess_LSTM = scalery.inverse_transform(mess_LSTM)*-1
mess_LSTM = pd.DataFrame(mess_LSTM)
mess_LSTM['sem'] = mess_LSTM.std(axis = 1, skipna = True)

mess_GRU = pd.DataFrame(test_pred_gru).transpose()
mess_GRU = scalery.inverse_transform(mess_GRU)*-1
mess_GRU = pd.DataFrame(mess_GRU)
mess_GRU['sem'] = mess_GRU.std(axis = 1, skipna = True)

mess_FFNN = pd.DataFrame(test_pred_ffnn).transpose()
mess_FFNN = scalery.inverse_transform(mess_FFNN)*-1
mess_FFNN = pd.DataFrame(mess_FFNN)
mess_FFNN['sem'] = mess_FFNN.std(axis = 1, skipna = True)

mess_LSTM_GRU = pd.DataFrame(test_pred_lstm_gru).transpose()
mess_LSTM_GRU = scalery.inverse_transform(mess_LSTM_GRU)*-1
mess_LSTM_GRU = pd.DataFrame(mess_LSTM_GRU)
mess_LSTM_GRU['sem'] = mess_LSTM_GRU.std(axis = 1, skipna = True)

mess_DBN_LSTM = pd.DataFrame(test_pred_dbn_lstm).transpose()
mess_DBN_LSTM = scalery.inverse_transform(mess_DBN_LSTM)*-1
mess_DBN_LSTM = pd.DataFrame(mess_DBN_LSTM)
mess_DBN_LSTM['sem'] = mess_DBN_LSTM.std(axis = 1, skipna = True)
pre_df.head()

In [ ]:

# #LSTM
E_low_L = pd.DataFrame(pre_df["LSTM_gwls"].values - mess_LSTM['sem'].values).set_index(year_test)
E_low_L.columns = ['lstm_low_err']

E_up_L = pd.DataFrame(pre_df["LSTM_gwls"].values + mess_LSTM['sem'].values).set_index(year_test)
E_up_L.columns = ['lstm_up_err']

# #GRU
E_low_G = pd.DataFrame(pre_df["GRU_gwls"].values - mess_GRU['sem'].values).set_index(year_test)
E_low_G.columns = ['gru_low_err']

E_up_G = pd.DataFrame(pre_df["GRU_gwls"].values + mess_GRU['sem'].values).set_index(year_test)
E_up_G.columns = ['gru_up_err']

# #GRU
E_low_F = pd.DataFrame(pre_df["FFNN_gwls"].values - mess_FFNN['sem'].values).set_index(year_test)
E_low_F.columns = ['ffnn_low_err']

E_up_F = pd.DataFrame(pre_df["FFNN_gwls"].values + mess_FFNN['sem'].values).set_index(year_test)
E_up_F.columns = ['ffnn_up_err']

# #LSTM-GRU
E_low_LG = pd.DataFrame(pre_df["LSTM_GRU_gwls"].values - mess_LSTM_GRU['sem'].values).set_index(year_test)
E_low_LG.columns = ['lstm_gru_low_err']

E_up_LG = pd.DataFrame(pre_df["LSTM_GRU_gwls"].values + mess_LSTM_GRU['sem'].values).set_index(year_test)
E_up_LG.columns = ['lstm_gru_up_err']

#DBN-LSTM
E_low_DL = pd.DataFrame(pre_df["DBN_LSTM_gwls"].values - mess_DBN_LSTM['sem'].values).set_index(year_test)
E_low_DL.columns = ['dbn_lstm_low_err']

E_up_DL = pd.DataFrame(pre_df["DBN_LSTM_gwls"].values + mess_DBN_LSTM['sem'].values).set_index(year_test)
E_up_DL.columns = ['dbn_lstm_up_err']

pre_df_full = pd.concat([pre_df, E_low_L, E_up_L,E_low_G,E_up_G,E_low_F,E_up_F, 
                    E_low_LG, E_up_LG, E_low_DL, E_up_DL], axis = 1)

the_df = pd.concat([train_output,pre_df_full], axis = 0)
the_df

In [ ]:
mg = the_df['actual_gwls'].fillna(the_df['actual_test_gwls'])
the_df = the_df.drop(["actual_gwls"], axis = 1)
the_df = the_df.drop(["actual_test_gwls"], axis = 1)


the_df["Actual_gwls"] = mg
the_df

In [ ]:
the_df['Actual_gwls'].plot(figsize=(20,10), fontsize=30,color='black', linewidth=3)
# the_df['actual_test_gwls'].plot(fontsize=15, color='black', linewidth=2)

the_df['LSTM_gwls'].plot(color='#E52B50', linewidth=3)
x = np.arange(len(the_df.index))
plt.fill_between(x, the_df['lstm_low_err'], the_df['lstm_up_err'], 
             color = '#9F2B68', alpha = 0.5)

the_df['GRU_gwls'].plot(color='#333399', linewidth=3)
x = np.arange(len(the_df.index))
plt.fill_between(x, the_df['gru_low_err'], the_df['gru_up_err'], 
             color = '#A2A2D0', alpha = 0.5)

the_df['FFNN_gwls'].plot(color='#665D1E', linewidth=3)
x = np.arange(len(the_df.index))
plt.fill_between(x, the_df['ffnn_low_err'], the_df['ffnn_up_err'], 
             color = '#CD9575', alpha = 0.5)

the_df['LSTM_GRU_gwls'].plot(color='#0048BA', linewidth=3)
# x = np.arange(len(the_df.index))
plt.fill_between(x, the_df['lstm_gru_low_err'], the_df['lstm_gru_up_err'], 
             color = '#72A0C1', alpha = 0.5)


the_df['DBN_LSTM_gwls'].plot(color='green', linewidth=3)
# x = np.arange(len(the_df.index))
plt.fill_between(x, the_df['dbn_lstm_low_err'], the_df['dbn_lstm_up_err'], 
             color = '#B0BF1A', alpha = 0.5)

plt.xlabel("Year",fontsize=30)
plt.ylabel("Groundwater level (mbgl)",fontsize=30)
# plt.xticks(the_df.index[0])
plt.title(bbh,fontsize=30)
plt.legend(loc='best', prop={'size': 20})
plt.savefig(figname, dpi=300)

In [ ]:
print(borehole)
print("\n")
print("DNB r2: ",dbn_r2_new)
print("LSTM r2: ",lstm_r2_new)
print("GRU r2: ",gru_r2_new)
print("FFNN r2: ",ffnn_r2_new)
print("LSTM-GRU r2: ",lstm_gru_r2_new)
print("DBN-LSTM r2: ",dbn_lstm_r2_new)

print("\n")
print("DNB mse: ",dbn_mse_new)
print("LSTM mse: ",lstm_mse_new)
print("GRU mse: ",gru_mse_new)
print("FFNN mse: ",ffnn_mse_new)
print("LSTM-GRU mse: ",lstm_gru_mse_new)
print("DBN-LSTM mse: ",dbn_lstm_mse_new)

## END